![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 13,14. <i>Korekta pisowni</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Współczesne programy typu CAT nie mogą obyć się bez korektora pisowni. Na bieżąco kontrolują one pisownię wyrazów po stronie docelowej, czyli tam, gdzie tłumacz wpisuje tłumaczenie. Jest to niezwykle istotne w sytuacji, gdy język docelowy nie jest dla tłumacza językiem ojczystym. Co więcej, badania wykazują, iż korekta pisowni wydatnie zmniejsza liczbę błędów w każdych scenariuszach.

Co poprawia korekta pisowni? Słowa. Tylko lub aż słowa. Program dokonujący korekty pisowni przegląda tekst słowo po słowie i sprawdza, czy należy ono do słownika. Jeśli nie, sygnalizowany jest błąd oraz, jeśli to możliwe, podawane sugestie poprawy. Co istotne, korektor pisowni nie zajmuje się szeregiem błędów, które mieszczą się w dziedzinie korekty gramatycznej, w tym:
* interpunkcją
* powtórzeniami wyrazów
* stylistyką.

Aby zaimplementować korektor pisowni bez wątpienia potrzebny jest słownik. Skorzystajmy ze słownika, który znajdziemy w folderze data, pochodzącego z narzędzia Hunspell. Jest on spakowany - użyjmy techniki czytania z archiwum zip bez rozpakowywania. Poniższy kod wypisze fragment ze środka słownika.

In [1]:
from zipfile import ZipFile

with ZipFile('data/hunspell_pl.zip') as zipped_dictionary:
    with zipped_dictionary.open('hunspell_pl.txt') as dictionary_file:
        count = 0
        for line_bytes in dictionary_file:
            count += 1
            if count >= 100000 and count <= 100020:
                line = line_bytes.decode('utf-8')
                print(line.rstrip())

kalecząc
kaledonidy
kaledoński
kalefaktor
kalejdofon
kalejdoskop
kalejdoskopowość
kalejdoskopowy
kaleka
kaleki
kalema
kalendarium
kalendarz
kalendarzowy
kalendarzyk
kalendy
kalenica
kalenicowy
kalepin
kalesonki
kalesony


Miejmy na uwadze, że powyższy słownik zawiera tylko formy podstawowe słowa, np. zawiera słowo "kalendarz", ale nie zawiera "kalendarze", "kalendarza", "kalendarzy" itp. 

Algorytm korekty pisowni na podstawie słownika powinien działać według następujących kroków:
1. Wczytanie słownika do zbioru (set)
2. Podział tekstu do korekty na słowa (podział po spacji)
3. Dla każdego słowa wypisać, czy jest ono poprawne (znajduje się w słowniku) czy nie.

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm korekty pisowni według powyższych wytycznych.

In [27]:
def load_data(zip_file_path):
    with ZipFile(zip_file_path) as zip_f:
        with zip_f.open('hunspell_pl.txt') as f:
            return set([line.strip().lower() for line in f.read().decode('utf-8').splitlines()])

def correct_words(sentence, dictionary):
    """
    0 - incorrect
    1 - correct
    """
    return [(word, 1) if word in dictionary
            else (word, 0)
            for word in sentence.lower().split()]


In [28]:
data = load_data('data/hunspell_pl.zip')
print(correct_words('Hakunamatata', data))
print(correct_words('Czy dobrze pisze', data))
print(correct_words('Ala ma kota', data))

[('hakunamatata', 0)]
[('czy', 1), ('dobrze', 1), ('pisze', 0)]
[('ala', 1), ('ma', 1), ('kota', 1)]


To jednak oczywiście nie wszystko. Do tej pory mamy funkcjonalność sygnalizowania słów błędnych, ale każdy dobry korektor pisowni potrafi podać sugestie poprawek. W tym celu musimy stawić czoła następującemu problemowi - wygenerowanie listy słów podobnych do danego słowa błędnego, które znajdują się w słowniku.

W pierwszej kolejności musimy zdefiniować podobieństwo między wyrazami. Posłuży do tego dobrze nam znana odległość Levenshteina - wyrazy podobne to takie, dla których dystans Levenshteina jest niewielki (np. równy 1 lub 2). Teraz brakuje tylko algorytmu wyszukiwania wyrazów w danym słowniku, które znajdują się niedaleko (w sensie Levenshteina) danego błędnego słowa.

Rozważmy następujący algorytm: dla danego słownika $D$ i błędnego słowa $w \notin D$:
1. Wygeneruj zbiór $L_1(w)$ wszystkich słów, których odległość Levenshteina od $w$ wynosi 1.
2. Wyznacz zbiór $S_1(w)=L_1(w) \cap D$
3. Wyznacz zbiór $L_2(w)=\bigcup_{v \in L_1(w)} L_1(v)$
4. Wyznacz zbiór $S_2(w)=L_2(w) \cap D$
5. Zwróć jako listę sugestii: $S_1 \cup S_2$

### Ćwiczenie 2: Napisz funkcję do generowania zbioru $L_1(w)$ - wszystkich słów znajdujących się w odległości Levenshteina 1 od danego słowa w.

In [33]:
alphabet = 'aąbcćdeęfghijklłmnńoóprsśtuwyzźż'

def L1(w):
    edits = set()
    for i in range(len(w) + 1):
        for c in alphabet:
            if i < len(w):
                edits.add(w[:i] + c + w[i+1:])
            edits.add(w[:i] + c + w[i:])
        if i < len(w):
            edits.add(w[:i] + w[i+1:])
    return edits

def L2(l1):
    edits = set()
    for word in l1:
        edits.update(L1(word))
    return edits

def S(edits, dictionary):
    return set(dictionary).intersection(set(edits))

### Ćwiczenie 3: Napisz funkcję do generowania sugestii poprawek dla danego słowa według opisanego wcześniej algorytmu.

In [39]:
def apply_edits(sentence, dictionary):
    suggestions = []
    for word, is_misspelled in sentence:
        if is_misspelled == 0:
            words = generate_suggestions(word, dictionary)
            suggestions.append(words)
        else:
            suggestions.append([word])
    return suggestions

def generate_suggestions(w, dictionary):
    l1 = L1(w)
    l2 = L2(l1)
    s1 = S(l1, dictionary)
    s2 = S(l2, dictionary)
    return s1.union(s2)

print(apply_edits(correct_words('Cześć mam na jajnek', data), data))

[['cześć'], ['mam'], ['na'], {'gajek', 'tajner', 'jasne', 'janne', 'jajem', 'janet', 'jacek', 'janez', 'banek', 'jarek', 'panek', 'ranek', 'majtek', 'danek', 'jadnak', 'jenek', 'najdek', 'jaje', 'jane', 'kajtek', 'jonek', 'jamnik', 'janik', 'pajek', 'janem', 'gajnik', 'jajnik', 'jasiek', 'garnek', 'majek', 'bajek', 'jasek', 'jasnej', 'janek', 'tajnik', 'ganek'}]
